## Aprendizaje no supervisado - Clustering
##### Inteligencia Artificial, Ingeniería de Sistemas
##### Prof. Hugo Franco

#### 1. Implementación básica del algoritmo K-means.

Se implementa la clase que representa los estados del juego para su evaluación durante la búsqueda. Se importa **numpy** (manipulación matricial), **matplotlib.pyplot** y **style** de **matplotlib** (gráficas)


In [ ]:
import numpy as np # Álgebra lineal
from matplotlib import pyplot as plt # Gráficas 
from copy import deepcopy # Copia de vectores de dimensión arbitraria por bloques
# Control de los plots en un cuadernillo interactivo
%matplotlib inline 

def K_means(data,k):
    #### K-means ####
    # Número de elementos del conjunto
    n = data.shape[0]
    # Dimensión de los datos 
    m = data.shape[1] # número de características de cada elemento del dataset y del centroide

    # Generar los centroides de forma aleatoria, dentro del área definida por la media y la desviación
    # estándar de los datos
    mean = np.mean(data, axis = 0)
    std = np.std(data, axis = 0)
    centroids = np.random.randn(k,m)*std + mean

    # posiciones de los centroides en el paso anterior
    centroids_prev = np.zeros(centroids.shape) 
    # posiciones de los centroides en el paso siguiente
    centroids_new = deepcopy(centroids) 

    # Etiquetas y distancias para cada uno de los elementos del dataset
    labels = np.zeros(n)
    distances = np.zeros((n,k))

    # La condición de parada se establece sobre la diferencia entre los centroides anteriores y los nuevos:
    # si no hay cambios en sus posiciones, no ha habido reetiquetado, luego el algoritmo para.
    error = np.linalg.norm(centroids_new - centroids_prev)
    iteration=0;

    # Si la estimación de los centroides no cambia, se termina el bucle de actualización 
    while error != 0:
        # Medir la distancia a cada centroide
        print ("Iteración: ", iteration, "Error: ", error)
        for i in range(k):
            # elemento por elemento, calcula su distancia del j-ésimo punto a su centroide
            # La sintaxis ":" representa un bucle implícito (operación "element-wise")
            distances[:,i] = np.linalg.norm(data - centroids_new[i], axis=1)

        # Asigna las etiquetas de cada cluster, la función argmin retorna los índices (valores de i)
        # correspondientes a las distancias ordenadas de menor a mayor.
        labels = np.argmin(distances, axis = 1)

        centroids_prev = deepcopy(centroids_new)
        # Calcula la nueva media para cada cluster y actualiza su centroide
        for i in range(k):
            centroids_new[i] = np.mean(data[labels == i], axis=0)

        # Se usa como criterio de convergencia la norma de la distancia entre los centroides anteriores y nuevos.
        error = np.linalg.norm(centroids_new - centroids_prev)
        iteration += 1

    return centroids_new,labels

Para este ejemplo, se generarán _aleatoriamente_ 3 grupos de datos bidimensionales. 

In [ ]:
# Se crean tres centros, el modelo debería retornar valores similares para los centroides calculados
center_1 = np.array([1,1])
center_2 = np.array([4,6])
center_3 = np.array([7,2])

# Se generan datos de forma aleatoria localizados alrededor de cada centro 
data_1 = np.random.randn(100,2) + center_1
data_2 = np.random.randn(100,2) + center_2
data_3 = np.random.randn(100,2) + center_3

data = np.concatenate((data_1, data_2, data_3), axis = 0)
print("Dataset original:")
plt.scatter(data[:,0], data[:,1], s=7)
plt.show()

Se ejecuta el método __K_means__ de sklearn, graficando la posición de los centroides determinada por dicho método.

In [ ]:
(centroids,labels)=K_means(data,3)
print("Elementos clasificados:")

print("Resultado de la clusterización:")
plt.scatter(data[:,0], data[:,1], c=labels, s=7 , cmap='viridis')
plt.scatter(centroids[:,0], centroids[:,1], marker='*',  s=150)
plt.show()

#### 2. Versión de SKLearn 

Kmeans se importa de **sklearn.cluster**, asociada a aprendizaje no supervisado (clustering). Aquí se presenta otra forma de representar los datos de entrada y las transformaciones necesarias sobre los datos

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import style
style.use("ggplot")
from sklearn.cluster import KMeans

Se declaran los arrays de coordenadas de los puntos (x,y) y se grafican con **matplotlib.pyplot**

In [ ]:
data_1 = np.random.randn(100,2) + center_1
data_2 = np.random.randn(100,2) + center_2
data_3 = np.random.randn(100,2) + center_3
data = np.concatenate((data_1, data_2, data_3), axis = 0)
x=data[:,0]
y=data[:,1]
plt.scatter(x,y,s=7)
plt.show()

Se construye el array de **numpy** que representa el *dataset* y puede ser usado como parámetro del método K-means en su implementación de **sklearn**, mediante la función de **numpy.column_stack**

In [ ]:
X=np.column_stack((x,y))
# Mostrar el 5 % de los datos
for i in range(int(len(X)*.05)):
    print (X[i])

Se inicializa un objeto KMeans con K=2, se ejecuta el algoritmo ajustando el dataset X usando la función **fit**, luego se obtienen las posiciones de los centroides con el atributo *cluster_centers_* del objeto *kmeans* y las etiquetas (clases, índice de cluster) con el atributo *labels_*

In [ ]:
kmeans=KMeans(n_clusters=3)
kmeans.fit(X)

centroids = kmeans.cluster_centers_
labels = kmeans.labels_

print(centroids)
print(labels)

Se presenta la salida del proceso de agrupamiento (clustering) y se grafican los puntos coloreados  según el cluster al que fueron asignados (azul para la clase 0, verde para la clase 1) y la posición de los centroides finales (*).

In [ ]:
# Mostrar el 5 % de los datos
for j in range(int(len(X)*.05)):
    print("coordenada:",X[j], "índice de cluster:", labels[j])


plt.scatter(X[:,0], X[:,1], c=labels, s=7, cmap='viridis')
plt.scatter(centroids[:, 0],centroids[:, 1], marker = "*", s=150, linewidths = 2, zorder = 10)

plt.show()

#### 3. Gráfica de codo (selección del mejor modelo)

Para la gráfica de codo, es necesario iterar por un conjunto de valores de _K_ de manera que se pueda seleccionar, por inspección visual, el valor a partir del cual agregar nuevos clusters no aporta una mejora significativa en el agrupamiento, según la función de costo _J_ 

In [ ]:
costo = []
for i in range(1,8):
    kmeans = KMeans(n_clusters=i,init="k-means++",max_iter=300,n_init=10,random_state=0)
    kmeans.fit(X)
    costo.append(kmeans.inertia_)
    print("Cluster", i, "Función de costo", kmeans.inertia_)

plt.plot(range(1,8),costo)
plt.title("Gráfica de codo")
plt.xlabel("Número de clusters")
plt.ylabel("Funcion de costo") 
plt.show()

Es posible observar el comportamiento del método a medida que aumenta $K$ (el número de clusters)

In [ ]:

for i in range(2,8): 
    kmeans=KMeans(n_clusters=i)
    kmeans.fit(X)

    centroids = kmeans.cluster_centers_
    labels = kmeans.labels_

    plt.scatter(X[:,0], X[:,1], c=labels, s=7, cmap='viridis')
    plt.scatter(centroids[:, 0],centroids[:, 1], marker = "*", s=150, linewidths = 2, zorder = 10)

    plt.show()
    i=i+1

#### 2. DBSCAN
El algoritmo DBSCAN también está implementado en __SKLearn__. En el siguiente ejemplo, se muestran sus ventajas respecto de algoritmos basados en centroides fijos como _KMeans_ o _Mezcla de Gaussianas_


In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# Se comparará el desempeño de DBSCAN vs. KMeans
from sklearn.cluster import DBSCAN
from sklearn.cluster import KMeans

Para el ejemplo de los arcos ("moons"), se puede usar el módulo de datasets de __sklearn__

In [ ]:
# se crean los clusters de ejemplo usando sklearn datasets
from sklearn.datasets import make_moons

data = make_moons(500, noise=0.055)[0]

# Estandarizar los datos a la media y la desviación estándar
for x in range(2):
    m = data[:,x].mean()
    s = data[:,x].std()
    for y in range(len(data)):
        data[y,x] = (data[y,x] - m)/s

# Resultado mediante KMeans
result_k = KMeans(n_clusters=2).fit(data)

centroids=result_k.cluster_centers_
labels = result_k.labels_
plt.scatter(data[:,0], data[:,1], c=labels, s=7 )
plt.scatter(centroids[:, 0],centroids[:, 1], marker = "+", s=150, linewidths = 2, zorder = 10)
plt.show()

# DBSCAN desde Scikit-Learn
dbscan = DBSCAN(eps=0.2, min_samples = 2)
clusters = dbscan.fit_predict(data)
plt.scatter(data[:, 0], data[:, 1], c=clusters, s=7, linewidths = 2, zorder = 10)

Se puede generar el mismo ejemplo patrón para un conjunto de anillos concéntricos.

In [ ]:
# se crean los clusters de ejemplo usando sklearn datasets
from sklearn.datasets import make_circles

data_a = make_circles(250, noise=0.055, factor=.9)[0]
data_b = make_circles(250, noise=0.055, factor=.4)[0]
data=np.concatenate((data_a, data_b), axis=0)

# Estandarizar los datos a la media y la desviación estándar
for x in range(2):
    m = data[:,x].mean()
    s = data[:,x].std()
    for y in range(len(data)):
        data[y,x] = (data[y,x] - m)/s

# Resultado mediante KMeans
result_k = KMeans(n_clusters=2).fit(data)

centroids=result_k.cluster_centers_
labels = result_k.labels_
plt.scatter(data[:,0], data[:,1], c=labels, s=7 )
plt.scatter(centroids[:, 0],centroids[:, 1], marker = "+", s=150, linewidths = 2, zorder = 10)
plt.show()

# DBSCAN desde Scikit-Learn
dbscan = DBSCAN(eps=0.2, min_samples = 2)
clusters = dbscan.fit_predict(data)
plt.scatter(data[:, 0], data[:, 1], c=clusters, s=7, linewidths = 2, zorder = 10)

#### 3. Mezcla de Gaussianas
Se crea un conjunto de ejemplo (en este caso, 4 clusters aleatorios) usando las funciones de la biblioteca __SKLearn__ (función _makeblobs_, en el futuro cambiará de ubicación en la estructura de la biblioteca)

In [ ]:
from sklearn.mixture import GaussianMixture as GMM
from sklearn.datasets import make_blobs
import matplotlib.pyplot as plt
# Control de los plots en un cuadernillo interactivo
%matplotlib inline 

X, y_true = make_blobs(n_samples=400, centers=4, cluster_std=0.70, random_state=0)
plt.scatter(X[:, 0], X[:, 1], s=7)
plt.show()

Se usa el método de mezcla de gaussianas de __SKLearn__

In [ ]:
the_gmm = GMM(n_components=4).fit(X)
labels = the_gmm.predict(X)
print("Clasificación no-supervisada mediante mezcla de gaussianas")
plt.scatter(X[:, 0], X[:, 1], c=labels, s=7, cmap='viridis');
plt.show()
print("Etiqueta original, de la generación de los datos aleatorios")
plt.scatter(X[:, 0], X[:, 1], c=y_true, s=7, cmap='viridis');
plt.show()

A continuación se presenta un ejemplo que permite graficar las elipsoides relacionadas (visualización tomada de _Python Data Science Handbook_)

In [ ]:
from matplotlib.patches import Ellipse

def draw_ellipse(position, covariance, ax=None, **kwargs):
    
    ax = ax or plt.gca()
    
    # Convierte la covarianza a ejes principales de una elipsoide 
    if covariance.shape == (2, 2):
        U, s, Vt = np.linalg.svd(covariance) # usa descomposición en valores singulares de la matriz de covarianza
        angle = np.degrees(np.arctan2(U[1, 0], U[0, 0])) #obtiene el ángulo del elipsoide 
        width, height = 2 * np.sqrt(s) #establece el ancho y el alto del elipsoide a dos veces la desviación estándar
    else:
        angle = 0
        width, height = 2 * np.sqrt(covariance)
    
    # Dibuja la elipse
    for nsig in range(1, 4):
        ax.add_patch(Ellipse(position, nsig * width, nsig * height,
                             angle, **kwargs))
        
def plot_gmm(gmm, X, label=True, ax=None):
    ax = ax or plt.gca()
    labels = gmm.fit(X).predict(X)
    if label:
        ax.scatter(X[:, 0], X[:, 1], c=labels, s=7, cmap='viridis', zorder=2)
    else:
        ax.scatter(X[:, 0], X[:, 1], s=7, zorder=2)
    ax.axis('equal')
    
    w_factor = 0.2 / gmm.weights_.max()
    for pos, covar, w in zip(gmm.means_, gmm.covariances_, gmm.weights_):
        draw_ellipse(pos, covar, alpha=w * w_factor)
        
plot_gmm(the_gmm,X)

__Actividad (Taller)__: aplicar los métodos de K-Means, Mezcla de Gaussianas y DBScan para identificar los tipos de especie de cada registro en el dataset Iris:

<pre>
from sklearn import datasets
iris = datasets.load_iris()
</pre>